In [ ]:
# Getting the Information of other ships:
# 1. Postions of their ships and amount of their halites
# 2. Postions of their Shipyards and the amount of its halite
# 3. Getting the amount of halites in each cell
# 4. Draw a map describing this whole features

In [1]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

In [142]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *
import numpy as np

# Create a test environment for use later
board_size = 21
environment = make("halite", configuration={"size": board_size, "startingHalite": 5000}, debug=True)
agent_count = 4
environment.reset(agent_count)
state = environment.state[0]
board = Board(state.observation, environment.configuration)

In [115]:
decider = Decesion_Ship(board, board.ships['0-1'], 100)
board.ships['0-1'].next_action = decider.determine()
board = board.next()

In [121]:
decider = Decesion_Ship(board, board.ships['2-1'], 100)
board.ships['2-1'].next_action = decider.determine()
board = board.next()

In [22]:
class Decesion_Ship:
    def __init__(self, board, ship, step):
        self.board = board
        self.step = step
        self.ship = ship
        self.ship_halite = ship.cell.halite
        self.keywords = ['GET_AWAY', 'DONT_GO']
        # player
        self.player = self.board.current_player
        self.moves = {"N": ShipAction.NORTH, 'S': ShipAction.SOUTH, 'W': ShipAction.WEST , 
                      'E' : ShipAction.EAST, 'convert': ShipAction.CONVERT,'mine': None}
        
        self.grid = self.grid_5()
        
        
    def determine(self):
        if len(self.player.shipyards) == 0:
            return self.moves['convert']
        
        weights = self.weight_moves()
        
        max_move = max(weights, key=weights.get)
        
        if 'mine' in self.moves.keys() and (self.ship.cell.halite) > weights[max_move]:
            return self.moves['mine']
        
        print(weights, (self.ship.cell.halite) ** (1.5))
        return self.moves[max_move]
        
    
    def weight_moves(self):
        """
            This functions weights different points based on their properties and
            returns a dictionary of weights to choose from.
        """
        
        # First stage: eliminations
        self.first_stage()
        weights = {}
        
        # Add the weight of all other point to the main four
        for Dir, cell in self.grid["1"].items():
            # Instantiate the weight for the Direction
#             print('Direction: ', Dir)
            own_weight = self.weight_cell(cell)
            weights[Dir] = own_weight
            
            # Go through all other ones
            for index in  range(2, 5):
                for sub_Dir, sub_cell in self.grid[str(index)].items():
                    if Dir in sub_Dir:
                        weights[Dir] += self.weight_cell(sub_cell)
                        
        return weights
                    
        
    
    def first_stage(self):
        """
            Eliminate some moves before weighting
            'DONT_GO': avoid that direction
            'GET_away': Dont stay in the current position and took one of the other path than this one
            '': just weight and see which one works better
        """
        
        # If there was a ship/shipyard in E,N,W,or E
        for Dir, cell in self.grid["1"].items():
            cell_ship = cell.ship
            cell_yard = cell.shipyard
            
            # If there is a ship:
            if cell_ship != None:
                # If it is one of my ships
                if cell_ship.id in self.player.ship_ids:
                    # 'DONT_GO'
                    del self.moves[Dir]
                else:
                    myCargo = self.ship.halite
                    oppCargo = cell_ship.halite
                    # If I had more cargo then get_away
                    if oppCargo < myCargo:
                        # 'GET_AWAY'
                        del self.moves[Dir]
                        del self.moves['mine']
                    
    
    def weight_cell(self, cell):
        """ Weights a cell only based on its properties and relative halite. """
        w = 0
        cell_ship = cell.ship
        cell_yard = cell.shipyard
        
        w += (cell.halite - self.ship_halite) + 2
        
#         print('0-w:', w)
        
        if cell_ship != None:
            if cell_ship.id in self.player.ship_ids:
                print('1: w: ', cell_ship.halite * -10)
                w += cell_ship.halite * -10
            else:
                myCargo = self.ship.halite
                oppCargo = cell_ship.halite
                
                print('2: w: ', (oppCargo - myCargo) * 8)
                w += (oppCargo - myCargo) * 8
                
        if cell_yard != None:
            if cell_yard.id in self.player.shipyard_ids:
#                 print('3: w:', ( self.ship.halite + 10) * 7)
                w += ( self.ship.halite + 10) * 7
            else:
                oppYards = len(cell_yard.player.shipyards)
#                 print('4: w:', 1 / (oppYards + 1) * 10)
                w += 1 / (oppYards + 1) * 10
        
        return w
                    
        
    
    def grid_5(self):
        """
            retuns a 5x5 dictionary as a dictionary
            1 means cells where you can reach with one move, etc.
        """
        north = self.ship.cell.north
        south = self.ship.cell.south
        west = self.ship.cell.west
        east = self.ship.cell.east
        
        nn = north.north
        ss = south.south
        ww = west.west
        ee = east.east
        
        return {
            '1': {'N': north, 'S': south, 'W': west, 'E': east}, 
            '2': {
                    'NW': north.west, 'NE': north.east, 'SW': south.west, 'SE': south.east,
                    'WW': ww, 'EE': ee, 'NN': nn, 'SS': ss
                },
            '3': {
                 'NEN': nn.east, 'NWN': nn.west, 'SES': ss.east, 'SWS': ss.west, 
                 'SEE': ee.south, 'NEE': ee.north, 'SWW': ww.south, 'NWW': ww.north
             },
            '4': {'SEES': ee.south.south , 'NEEN': ee.north.north, 'NWWN': ww.north.north, 'SWWS': ww.south.south}
        }

In [24]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *
acts = {
    "N": ShipAction.NORTH, 'S': ShipAction.SOUTH,
    'W': ShipAction.WEST , 'E' : ShipAction.EAST,
    'spawn': ShipyardAction.SPAWN, 'convert': ShipAction.CONVERT,
    'mine': None
}

# Create a test environment for use later
board_size = 21
environment = make("halite", configuration={"size": board_size, "startingHalite": 5000}, debug=True)
agent_count = 4
environment.reset(agent_count)
state = environment.state[0]
board = Board(state.observation, environment.configuration)
for i in range(30):
    player = board.current_player
#     print(player.shipyards, end='')
    
    if len(player.ships) != 0:
        decider = Decesion_Ship(board, player.ships[0], 100)
        player.ships[0].next_action = decider.determine()
    else:
        for shipyard in player.shipyards:
            shipyard.next_action = acts['spawn']
    
    print(player.next_actions)
    
    board = board.next()

{'0-1': 'CONVERT'}
{'1-1': 'SPAWN'}
{'N': 78.263, 'S': 128.202, 'W': 101.15200000000002, 'E': 111.55500000000002} 0.0
{'2-1': 'SOUTH'}
{'N': 67.46099999999997, 'S': -3.600000000000012, 'W': 5.950999999999988, 'E': 43.09299999999999} 28.654452019607707
{'2-1': 'NORTH'}
{'N': 80.617, 'S': 132.381, 'W': 104.43, 'E': 115.253} 0.0
{'2-1': 'SOUTH'}
{'N': 68.46399999999998, 'S': -2.641000000000007, 'W': 7.295999999999994, 'E': 45.937999999999995} 29.51707152057941
{'2-1': 'NORTH'}
{'N': 83.067, 'S': 136.72500000000002, 'W': 107.841, 'E': 119.101} 0.0
{'2-1': 'SOUTH'}
{'N': 69.54299999999996, 'S': -1.6060000000000159, 'W': 8.73199999999999, 'E': 48.93499999999999} 30.40690294140461
{'2-1': 'NORTH'}
{'N': 85.615, 'S': 141.243, 'W': 111.39, 'E': 123.106} 0.0
{'2-1': 'SOUTH'}
{'N': 70.703, 'S': -0.49399999999998734, 'W': 10.262000000000006, 'E': 52.091000000000015} 31.324412523669135
{'2-1': 'NORTH'}
{'N': 88.26599999999999, 'S': 145.93899999999996, 'W': 115.083, 'E': 127.27199999999999} 0.0
{'2-

In [149]:
board.current_player.shipyards

In [109]:
for uid, ship in board.ships.items():
    print(uid, ship.cell.position)

2-1 (5, 16)
0-2 (15, 15)
0-3 (5, 5)
0-4 (15, 5)


In [45]:
board.ships[ids[0]].next_action = ShipAction.CONVERT
board = board.next()


In [46]:
print(board)

| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0A| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |b0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 

In [3]:
ship = next(iter(board.ships.values()))
ship.next_action = ShipAction.CONVERT
board = board.next()

print(board)
shipyard = list(board.shipyards.values())[0]
shipyard.next_action = ShipyardAction.SPAWN
board = board.next()

print(board)
# ship = list(board.ships.values())[0]
ship = board.ships['2-1']
ship.next_action = ShipAction.NORTH
board = board.next()

print(board)

| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0A| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |b0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 

In [59]:
board.observation['players']

[[4501, {'8-1': 110}, {}],
 [5000, {}, {'0-2': [120, 1]}],
 [5000, {}, {'0-3': [320, 1]}],
 [5000, {}, {'0-4': [330, 1]}]]

In [13]:
ship = next(iter(board.ships.values()))
ship.position

(5, 15)

In [47]:
b_cell = board.cells[(10, 10)]
north = b_cell.north
north_west = north
south = b_cell.south
east = b_cell.east
west = b_cell.west

In [41]:
print(b_cell.position)
print(north.position)
print(south.position)
print(east.position)
print(west.position)

(10, 10)
(10, 11)
(10, 9)
(11, 10)
(9, 10)


In [63]:
b_cell.neighbor(Point(0, 1)).position

(10, 11)

In [112]:
stats = {}
# max(stats, key=stats.get)
len(stats)

0

In [58]:
board.players[0].ship_ids

['0-1']

In [61]:
b_cell.ship_id == None

True

In [77]:


acts['N']

<ShipAction.NORTH: 1>

In [33]:
%%writefile attacker.py

from kaggle_environments.envs.halite.helpers import *

def get_neighbors(cell):
    # returns sorounding cells for a point
    return {
        'N': cell.north, 'NW': cell.north.west, 'NE': cell.north.east,
        'S': cell.south, 'SW': cell.south.west, 'SE': cell.south.east,
        'W': cell.west, 'E': cell.east
    }

def grid(cell):
    pass

actions = {
    "N": ShipAction.NORTH, "S": ShipAction.SOUTH,
    "W": ShipAction.WEST, "E": ShipAction.EAST,
    "convert": ShipAction.CONVERT, "spawn": ShipyardAction.SPAWN,
    "mine": None
}

def atttacker(obs, config):
    # Get the player's halite, shipyard, and ships 
    player_halite, shipyards, ships = obs.players[obs.player]
    size = config["size"]
    
    # Get the board object
    board = Board(obs, config)
    
    # Initialize a dictionary containing commands that will be sent to the game
    action = {}

    # If there are no ships, use first shipyard to spawn a ship.
    if len(ships) == 0 and len(shipyards) > 0:
        uid = list(shipyards.keys())[0]
        action[uid] = "SPAWN"
        
    # If there are no shipyards, convert first ship into shipyard.
    if len(shipyards) == 0 and len(ships) > 0:
        uid = list(ships.keys())[0]
        action[uid] = "CONVERT"
        
    for uid, ship in ships.items():
        if uid not in action: # Ignore ships that will be converted to shipyards
            pos, cargo = ship # Get the ship's position and halite in cargo
            
            ### Part 1: Set the ship's state 
            if cargo < 200: # If cargo is too low, collect halite
                ship_states[uid] = "COLLECT"
            if cargo > 500: # If cargo gets very big, deposit halite
                ship_states[uid] = "DEPOSIT"
                
            ### Part 2: Use the ship's state to select an action
            if ship_states[uid] == "COLLECT":
                # If halite at current location running low, 
                # move to the adjacent square containing the most halite
                if obs.halite[pos] < 100:
                    best = argmax(getAdjacent(pos, size), key=obs.halite.__getitem__)
                    action[uid] = DIRS[best]
            
            if ship_states[uid] == "DEPOSIT":
                # Move towards shipyard to deposit cargo
                direction = getDirTo(pos, list(shipyards.values())[0], size)
                if direction: action[uid] = direction
        board = board.next()
                
    return action

Overwriting attacker.py


In [4]:
str(2)

'2'

In [54]:
dic = {'a': 1, 'b': 2}
'a' in dic.keys()

True

In [113]:
%%writefile attacker_c.py

from kaggle_environments.envs.halite.helpers import *

class Decesion_Ship:
    def __init__(self, board, ship, step):
        self.board = board
        self.step = step
        self.ship = ship
        self.ship_halite = ship.cell.halite
        self.keywords = ['GET_AWAY', 'DONT_GO']
        # player
        self.player = self.board.current_player
        self.moves = {"N": ShipAction.NORTH, 'S': ShipAction.SOUTH, 'W': ShipAction.WEST , 
                      'E' : ShipAction.EAST, 'convert': ShipAction.CONVERT,'mine': None}
        
        self.grid = self.grid_5()
        
        
    def determine(self):
#         if self.step > 390:
#             print('over 390')
#             return self.moves['convert']  
        
        if len(self.player.shipyards) == 0 or self.step > 393:
            return self.moves['convert'] 
        
        if self.ship.halite > 2500:
            return self.moves['convert']  
        
        weights = self.weight_moves()
        if len(weights) > 0:
            max_move = max(weights, key=weights.get)
        else:
            return self.moves['mine']
        
        if 'mine' in self.moves.keys() and (self.ship.cell.halite) > weights[max_move]:
            return self.moves['mine']
        
        return self.moves[max_move]
        
    
    def weight_moves(self):
        """
            This functions weights different points based on their properties and
            returns a dictionary of weights to choose from.
        """
        # ADD the 1 2 3 4 moves
        # First stage: eliminations
        self.first_stage()
        weights = {}
        
        # Add the weight of all other point to the main four
        for Dir, cell in self.grid["1"].items():
            
            if Dir in self.moves.keys(): 
                # Instantiate the weight for the Direction
                own_weight = self.weight_cell(cell)
                weights[Dir] = own_weight

                # Go through all other ones
                for index in  range(2, 5):
                    for sub_Dir, sub_cell in self.grid[str(index)].items():
                        if Dir in sub_Dir:
                            weights[Dir] += self.weight_cell(sub_cell)
                            
        return weights
                    
    
    def first_stage(self):
        """
            Eliminate some moves before weighting
            'DONT_GO': avoid that direction
            'GET_away': Dont stay in the current position and took one of the other path than this one
            '': just weight and see which one works better
        """
        
        # If there was a ship/shipyard in E,N,W,or E
        for Dir, cell in self.grid["1"].items():
            cell_ship = cell.ship
            cell_yard = cell.shipyard
            
            # If there is a ship:
            if cell_ship != None:
                # If it is one of my ships
                if cell_ship.id in self.player.ship_ids:
                    # 'DONT_GO'
                    del self.moves[Dir]
                else:
                    myCargo = self.ship.halite
                    oppCargo = cell_ship.halite
                    # If I had more cargo then get_away
                    if oppCargo < myCargo:
                        # 'GET_AWAY'
                        del self.moves[Dir]
                        # To avoid errors first check to see if the value is there or not
                        if 'mine' in self.moves.keys():
                            del self.moves['mine']
                        
                    
    
    def weight_cell(self, cell):
        """ Weights a cell only based on its properties and relative halite. """
        w = 0
        cell_ship = cell.ship
        cell_yard = cell.shipyard
        
        w += (cell.halite - self.ship_halite) + 2
        
        if cell_ship != None:
            if cell_ship.id in self.player.ship_ids:
                w += cell_ship.halite * -10
            else:
                myCargo = self.ship.halite
                oppCargo = cell_ship.halite
                
                w += (oppCargo - myCargo) * 8
                
        if cell_yard != None:
            if cell_yard.id in self.player.shipyard_ids:
                w += ( self.ship.halite + 10) * 7
            else:
                oppYards = len(cell_yard.player.shipyards)
                w += 1 / (oppYards + 1) * 10
        
        return round(w, 3)
                    
        
    
    def grid_5(self):
        """
            retuns a 5x5 dictionary as a dictionary
            1 means cells where you can reach with one move, etc.
        """
        north = self.ship.cell.north
        south = self.ship.cell.south
        west = self.ship.cell.west
        east = self.ship.cell.east
        
        nn = north.north
        ss = south.south
        ww = west.west
        ee = east.east
        
        return {
            '1': {'N': north, 'S': south, 'W': west, 'E': east}, 
            '2': {
                    'NW': north.west, 'NE': north.east, 'SW': south.west, 'SE': south.east,
                    'WW': ww, 'EE': ee, 'NN': nn, 'SS': ss
                },
            '3': {
                 'NEN': nn.east, 'NWN': nn.west, 'SES': ss.east, 'SWS': ss.west, 
                 'SEE': ee.south, 'NEE': ee.north, 'SWW': ww.south, 'NWW': ww.north
             },
            '4': {'SEES': ee.south.south , 'NEEN': ee.north.north, 'NWWN': ww.north.north, 'SWWS': ww.south.south}
        }
        

def get_neighbors(cell):
    # returns sorounding cells for a point
    return {
        'N': cell.north, 'NW': cell.north.west, 'NE': cell.north.east,
        'S': cell.south, 'SW': cell.south.west, 'SE': cell.south.east,
        'WW': cell.west.west, 'EE': cell.east.east,
        'NN': cell.north.north, 'SS': cell.south.south,
        'W': cell.west, 'E': cell.east
    }

acts = {
    "N": ShipAction.NORTH, 'S': ShipAction.SOUTH,
    'W': ShipAction.WEST , 'E' : ShipAction.EAST,
    'spawn': ShipyardAction.SPAWN, 'convert': ShipAction.CONVERT,
    'mine': None
}

def randomize(choices=[]):
    import random
    
    if len(choices) == 0:
        choices = list(acts.items())
    
    choice = random.choice(choices)
    
    if choice[0] == 'spawn' or  choice[0] == 'convert':
        return randomize(exclude)
    
    return choice[1]


def choose_between(l=[]):
    import random
    
    if l != []:
        random.choice(l)
    
    return random.choice([acts['N'], acts['W'],acts['E'],acts['S'], acts['mine']])


def agent(obs, config):
    # Make the board
    board = Board(obs,config)
    #Step of the baord
    step = board.observation['step']
    # Current player info
    me = board.current_player # Player Object
    
    new_board = Board(obs,config)
    
    for ship in me.ships:
        
#         decider = Decesion_Ship(new_board, ship, step)
        decider = Decesion_Ship(new_board, new_board.ships[ship.id], step)
        ship.next_action = decider.determine()
        
        new_board = board.next()
    
    #Implemenet a pipeline where given that
    for shipyard in me.shipyards:
        # If there were no ships on the yard
        if new_board.shipyards[shipyard.id].cell.ship == None and step < 392:
            if len(me.ships) == 0:
                shipyard.next_action = acts['spawn']

            if step < 100 and step % 3 == 1:
                shipyard.next_action = acts['spawn']

            if step > 200 and me.halite > 10000 + len(me.ships) * 1000:
                shipyard.next_action = acts['spawn']
        
        new_board = board.next()

        
    return me.next_actions


Overwriting attacker_c.py


In [114]:
env = make("halite", debug=True)
env.run(["Agent_b.py", "attacker_c.py", 'Agent_b.py', 'Agent_b.py'])
env.render(mode="ipython", width=800, height=600)

In [ ]:
env = make("halite", debug=True)
env.run(["Agent_b.py", "attacker_c.py", 'attacker_c.py', 'Agent_b.py'])
env.render(mode="ipython", width=800, height=600)